In [14]:
import warnings
import itertools
import pandas as pd
import numpy as np
import statsmodels.api as sm
import matplotlib.pyplot as plt
import cProfile

from itertools import islice, takewhile, chain
from functools import reduce
from typing import Optional
import datetime as dt
from dataclasses import asdict, fields
from importlib import reload

from geopy.distance import distance
from shapely.geometry import Point, LineString
import shapely.geometry as sg
import geopandas as gpd

from typing import List
import ipyleaflet as lf
import statsmodels.api as sm
from statsmodels.tsa.arima_model import ARIMA

pd.set_option('display.max_rows', 1000000000)
pd.set_option('display.max_columns', None)
pd.set_option('max_colwidth', 160)

In [15]:
import busboy.model as m
import busboy.geo as geo
import busboy.database as db
import busboy.prediction as prediction
import busboy.prediction.pandas
import busboy.prediction.sklearn
import busboy.map.map as bmap
import busboy.apis as api
import busboy.util as util
import busboy.util.notebooks as notebook

In [16]:
reload(util)
reload(geo)
reload(m)
reload(db)
reload(prediction)
reload(busboy.prediction.pandas)
reload(busboy.prediction.sklearn)
reload(bmap)
reload(api)
reload(notebook)

<module 'busboy.util.notebooks' from '/Users/Noel/Developer/Projects/Busboy/busboy/util/notebooks.py'>

In [17]:
from sklearn.base import BaseEstimator, TransformerMixin
from sklearn.pipeline import Pipeline
from sklearn.dummy import DummyRegressor

from sklearn.model_selection import cross_val_score

# Class, for use in pipelines, to select certain columns from a DataFrame and convert to a numpy array
# From A. Geron: Hands-On Machine Learning with Scikit-Learn & TensorFlow, O'Reilly, 2017
# Modified by Derek Bridge to allow for casting in the same ways as pandas.DatFrame.astype
class DataFrameSelector(BaseEstimator, TransformerMixin):
    def __init__(self, attribute_names, dtype=None):
        self.attribute_names = attribute_names
        self.dtype = dtype
    def fit(self, X, y=None):
        return self
    def transform(self, X):
        X_selected = X[self.attribute_names]
        if self.dtype:
            return X_selected.astype(self.dtype).values
        return X_selected.values

In [27]:
rbn = db.routes_by_name()
route_name = "202"
route = rbn[route_name]
entries = db.snapshots(
    r=route.id, 
#     date_span=(dt.date(2019, 3, 2), dt.date(2019, 3, 9))
#     d=dt.date(2019, 3, 2)
)
stops_by_name = db.stops_by_name()
timetables = [t.value for t in db.timetables(route.id) if isinstance(t, util.Right)]
timetable_variants = {t for timetable in timetables for t in timetable.variants}

In [28]:
len(entries)

3469003

In [29]:
entries_by_vehicle = util.dict_collect_list(entries, lambda e: e.vehicle)
vehicles_by_entry_count = [v for (v, es) in sorted(entries_by_vehicle.items(), key = lambda t: len(t[1]), reverse=True)]

In [ ]:
route_sections = {
    variant: list(prediction.route_sections(variant.stops)) 
    for variant in timetable_variants
}

In [ ]:
def get_all_journeys(entries_by_vehicle, timetable_variants):
    return [
        prediction.sklearn.journeys(entries_by_vehicle[vehicle], timetable_variants, route_sections) 
        for vehicle in vehicles_by_entry_count
        if vehicle.raw is not None
    ]

In [ ]:
all_journeys = get_all_journeys(entries_by_vehicle, timetable_variants)

In [ ]:
prediction.cached_contains.cache_info()

In [ ]:
big_dfs = prediction.sklearn.join_journeys(all_journeys)
day_df = max(big_dfs.items(), key=lambda t: len(t[0].stops))
day_df[1]

In [ ]:
# day_df[1].to_csv("/Users/Noel/Developer/Projects/Busboy/data/220_preprocessed_1.csv")

for index, df in enumerate(big_dfs.values(), 1):
    df.to_csv(f"/Users/Noel/Developer/Projects/Busboy/data/{route_name}-preprocessed-{index}.csv")

In [5]:
dfs = notebook.read_preprocessed_data("220")
day_df = max(dfs, key=lambda tpl: len(tpl[0].stops))

In [6]:
last = f"{day_df[0].stops[5].name} [departure]"
target = f"{day_df[0].stops[55].name} [arrival]"
df = day_df[1]
df = df[pd.notnull(df[target]) & pd.notnull(df[last])]
# df = df[df[last] != df[target]] # should I drop these or not?
travel_times = prediction.pandas.travel_times(
    df, [], 
    last, 
    target)
travel_times_df = prediction.pandas.travel_times_df(df, last, target).set_index("start_time")

In [77]:
travel_times_df.sort_index()

end_time            travel_time
start_time                                                                  
2019-02-08 14:12:30.753912 2019-02-08 15:36:44.637110 0 days 01:24:13.883198
2019-02-08 15:01:39.902710 2019-02-08 16:47:47.342827 0 days 01:46:07.440117
2019-02-08 15:15:33.855262 2019-02-08 16:57:27.714466 0 days 01:41:53.859204
2019-02-08 15:16:23.890391 2019-02-08 16:52:37.540496 0 days 01:36:13.650105
2019-02-09 12:25:08.853382 2019-02-09 12:54:40.137125 0 days 00:29:31.283743
2019-02-09 12:33:19.205097 2019-02-09 13:41:41.910550 0 days 01:08:22.705453
2019-02-09 12:46:29.804326 2019-02-09 13:18:41.025833 0 days 00:32:11.221507
2019-02-09 13:02:00.418436 2019-02-09 14:17:33.395396 0 days 01:15:32.976960
2019-02-09 13:21:31.133452 2019-02-09 13:52:42.379273 0 days 00:31:11.245821
2019-02-10 21:32:29.474367 2019-02-10 22:34:52.244570 0 days 01:02:22.770203
2019-02-10 21:46:10.069874 2019-02-10 22:32:32.124056 0 days 00:46:22.054182
2019-02-10 21:52:40.286689 2019-02-10 22:15:11.353922 0 days 00:22:31.067233
2019-02-10 22:02:30.747881 2019-02-10 22:58:13.218330 0 days 00:55:42.470449
2019-02-10 22:30:32.031906 2019-02-10 23:10:53.850946 0 days 00:40:21.819040
2019-02-10 22:47:12.743690 2019-02-10 23:32:14.836884 0 days 00:45:02.093194
2019-02-10 23:14:04.012681 2019-02-10 23:58:56.099927 0 days 00:44:52.087246
2019-02-10 23:32:54.861158 2019-02-11 00:16:16.799839 0 days 00:43:21.938681
2019-02-11 00:00:16.137305 2019-02-11 00:42:38.043700 0 days 00:42:21.906395
2019-02-11 00:30:57.526604 2019-02-11 01:29:20.288541 0 days 00:58:22.761937
2019-02-11 01:11:39.433683 2019-02-11 02:07:22.020761 0 days 00:55:42.587078
2019-02-11 01:35:00.551341 2019-02-11 02:33:15.104848 0 days 00:58:14.553507
2019-02-11 02:53:35.969939 2019-02-11 03:47:18.589580 0 days 00:53:42.619641
2019-02-11 03:40:18.253246 2019-02-11 04:22:00.358548 0 days 00:41:42.105302
2019-02-11 04:40:41.241799 2019-02-11 05:22:43.309121 0 days 00:42:02.067322
2019-02-11 05:36:43.998523 2019-02-11 06:21:45.999103 0 days 00:45:02.000580
2019-02-11 06:17:05.762648 2019-02-11 07:06:27.980423 0 days 00:49:22.217775
2019-02-11 06:32:06.463098 2019-02-11 07:28:39.024608 0 days 00:56:32.561510
2019-02-11 07:21:48.694422 2019-02-11 08:40:12.025353 0 days 01:18:23.330931
2019-02-11 07:31:39.182570 2019-02-11 08:07:20.683519 0 days 00:35:41.500949
2019-02-11 07:34:29.311971 2019-02-11 08:59:32.826881 0 days 01:25:03.514910
2019-02-11 07:49:29.948487 2019-02-11 09:08:33.172156 0 days 01:19:03.223669
2019-02-11 08:35:51.818788 2019-02-11 09:38:44.292113 0 days 01:02:52.473325
2019-02-11 09:18:33.482110 2019-02-11 10:20:35.827588 0 days 01:02:02.345478
2019-02-11 09:21:33.582684 2019-02-11 10:20:55.830593 0 days 00:59:22.247909
2019-02-11 09:34:14.094579 2019-02-11 10:34:06.414229 0 days 00:59:52.319650
2019-02-11 09:49:14.633122 2019-02-11 10:53:57.184730 0 days 01:04:42.551608
2019-02-11 10:34:16.418452 2019-02-11 11:36:23.357081 0 days 01:02:06.938629
2019-02-11 10:49:57.079413 2019-02-11 11:51:38.474872 0 days 01:01:41.395459
2019-02-11 11:01:37.428743 2019-02-11 12:06:29.019254 0 days 01:04:51.590511
2019-02-11 11:15:38.014482 2019-02-11 12:17:49.480387 0 days 01:02:11.465905
2019-02-11 11:36:23.357081 2019-02-11 12:45:50.594359 0 days 01:09:27.237278
2019-02-11 12:09:49.139754 2019-02-11 13:09:01.419951 0 days 00:59:12.280197
2019-02-11 12:20:49.600314 2019-02-11 13:27:22.102467 0 days 01:06:32.502153
2019-02-11 12:32:10.032456 2019-02-11 13:42:02.652835 0 days 01:09:52.620379
2019-02-11 12:38:40.284756 2019-02-11 13:09:51.440829 0 days 00:31:11.156073
2019-02-11 12:59:11.100058 2019-02-11 14:03:13.549841 0 days 01:04:02.449783
2019-02-11 13:01:21.189994 2019-02-11 14:13:03.914362 0 days 01:11:42.724368
2019-02-11 13:17:11.698827 2019-02-11 14:20:54.240351 0 days 01:03:42.541524
2019-02-11 13:48:12.902457 2019-02-11 15:04:46.018071 0 days 01:16:33.115614
2019-02-11 14:21:54.274029 2019-02-11 15:22:56.648349 0 days 01:01:02.374320
2019-02-11 14:31:34.691238 2019-02-11 15:

In [21]:
y = travel_times.astype("int64") / 1_000_000_000
y

array([   0.      , 1340.912751, 1180.873781, ...,  800.529389,
        811.04528 ,  780.509215])

In [22]:
len(y)

1396

In [23]:
np.median(y)

1120.7271580000001

In [24]:
pipeline = Pipeline([
    ("selector", DataFrameSelector(list(df))),
    ("estimator", DummyRegressor(strategy="median")),
])
mean_error = np.mean(cross_val_score(pipeline, df, y, scoring="neg_mean_absolute_error", cv=4))
-mean_error

5435.878140000001

In [41]:
import datetime
time1 = datetime.datetime(2019, 2, 18, 11, 45, 12)
time2 = datetime.datetime(2019, 3, 1, 10, 22, 18)
test_times1 = np.array([time1], dtype="datetime64[us]")
test_times2 = np.array([time2], dtype="datetime64[us]")
a = test_times2 - test_times1
mean = a.mean()
average = np.average(a)

ValueError: Could not convert object to NumPy timedelta

In [12]:
a.mean()
np.average(a)

ValueError: Could not convert object to NumPy timedelta

In [180]:
avg = a.mean(0)
print(avg.size)
print(avg)
size_ratio = a.size/avg.size
type(size_ratio)
avg.dtype.type(int(size_ratio))
avg
np.median(a)

1
1160500000 microseconds


numpy.timedelta64(1160500000,'us')

In [53]:
to_time = lambda d: d.time().isoformat()
for variant, these_stop_times in times.items():
    print(f"Variant: {variant}")
    print(f"{len(these_stop_times)} journeys")
    for trip_number, trip_times in enumerate(these_stop_times):
        for stop_number, stop_time in enumerate(trip_times):
            to_time = lambda d: d.time().isoformat()
            try:
                stop_name = variant.stops[stop_number].name
            except IndexError:
                stop_name = "(IndexError)"
            print(f"- {trip_number}, {stop_number:2}, {stop_name:40}"
                  f" {stop_time.last_before.map(to_time).or_else(''):15}, {stop_time.first_after.map(to_time).or_else(''):15}")

Variant: (route: 201, start: Boherboy Rd (Opp Scoil Mhuire Banrion), end: CUH (Bishopstown Rd))
21 journeys
- 0,  0, Boherboy Rd (Opp Scoil Mhuire Banrion)                  , 07:19:32.536890
- 0,  1, Boherboy Road (Lotabeg Estate)           07:18:52.525808, 07:20:32.577308
- 0,  2, North Ring Road (Opp Mayfield Supermarke 07:20:12.559419, 07:21:32.628519
- 0,  3, North Ring Road (Lagan Grove)            07:21:32.628519, 07:22:52.652098
- 0,  4, North Ring Rd (Glencree Crescent)        07:22:52.652098, 07:23:32.658942
- 0,  5, North Ring Rd (Corrib Lawn)              07:23:32.658942, 07:24:32.690832
- 0,  6, North Ring Rd (Boyne Crescent)           07:24:32.690832, 07:25:12.698864
- 0,  7, North Ring Rd (Opp Riverview Estate)     07:25:52.734574, 07:27:32.789463
- 0,  8, Old Commons Rd (Opp Topaz Service St)    07:29:32.858933, 07:30:52.904094
- 0,  9, Farranferris Ave (Pophams Rd Junction)   07:30:52.904094, 07:32:32.993772
- 0, 10, Pophams Rd (Opposite Community Centre)   07:31:52.958

In [7]:
themap = bmap.Map()
themap.map

Map(basemap={'url': 'https://{s}.tile.openstreetmap.org/{z}/{x}/{y}.png', 'max_zoom': 19, 'attribution': 'Map …

In [10]:
themap.map.save("map.html")

AttributeError: 'Map' object has no attribute 'save'

In [8]:
rbn = db.routes_by_name()
route = rbn["220"]
timetables = [t.value for t in db.timetables(route.id) if isinstance(t, util.Right)]
notebook.show_timetables(themap, timetables)

In [9]:
themap.map.add_control(lf.LayersControl())

In [52]:
[(v, len(entries_by_vehicle[v])) for v in vehicles_by_entry_count]

[(VehicleId(raw='7338674957838189376'), 7885), (VehicleId(raw=None), 658)]

In [81]:
np.asarray(travel_times_df.astype("int64")).dtype

dtype('int64')

In [8]:
travel_times_df.resample("D").mean()

DataError: No numeric types to aggregate

In [29]:
travel_times = travel_times_df["travel_time"].astype("int64").dropna().resample("30s").mean().interpolate()
travel_times

start_time
2019-02-08 14:12:30    5.053883e+12
2019-02-08 14:13:00    5.067287e+12
2019-02-08 14:13:30    5.080690e+12
2019-02-08 14:14:00    5.094094e+12
2019-02-08 14:14:30    5.107498e+12
2019-02-08 14:15:00    5.120901e+12
2019-02-08 14:15:30    5.134305e+12
2019-02-08 14:16:00    5.147709e+12
2019-02-08 14:16:30    5.161112e+12
2019-02-08 14:17:00    5.174516e+12
2019-02-08 14:17:30    5.187920e+12
2019-02-08 14:18:00    5.201323e+12
2019-02-08 14:18:30    5.214727e+12
2019-02-08 14:19:00    5.228131e+12
2019-02-08 14:19:30    5.241534e+12
2019-02-08 14:20:00    5.254938e+12
2019-02-08 14:20:30    5.268341e+12
2019-02-08 14:21:00    5.281745e+12
2019-02-08 14:21:30    5.295149e+12
2019-02-08 14:22:00    5.308552e+12
2019-02-08 14:22:30    5.321956e+12
2019-02-08 14:23:00    5.335360e+12
2019-02-08 14:23:30    5.348763e+12
2019-02-08 14:24:00    5.362167e+12
2019-02-08 14:24:30    5.375571e+12
2019-02-08 14:25:00    5.388974e+12
2019-02-08 14:25:30    5.402378e+12
2019-02-08 14:26:

In [37]:
from random import sample
arima_predictor = ARIMA(travel_times_df["travel_time"].astype("int64").resample("30s").mean().interpolate(), (1,1,1))

In [38]:
fit = arima_predictor.fit()
fit.summary()

<class 'statsmodels.iolib.summary.Summary'>
"""
                             ARIMA Model Results                              
==============================================================================
Dep. Variable:          D.travel_time   No. Observations:                78731
Model:                 ARIMA(1, 1, 1)   Log Likelihood            -2248922.938
Method:                       css-mle   S.D. of innovations   615497719133.271
Date:                Fri, 22 Mar 2019   AIC                        4497853.876
Time:                        15:35:45   BIC                        4497890.971
Sample:                    02-08-2019   HQIC                       4497865.256
                         - 03-07-2019                                         
=======================================================================================
                          coef    std err          z      P>|z|      [0.025      0.975]
---------------------------------------------------------------------------------------
const               -2.327e+07   6.03e+09     -0.004      0.997   -1.18e+10    1.18e+10
ar.L1.D.travel_time     0.3930      0.004     93.927      0.000       0.385       0.401
ma.L1.D.travel_time     0.6675      0.004    171.895      0.000       0.660       0.675
                                    Roots                                    
=============================================================================
                  Real          Imaginary           Modulus         Frequency
-----------------------------------------------------------------------------
AR.1            2.5446           +0.0000j            2.5446            0.0000
MA.1           -1.4981           +0.0000j            1.4981            0.5000
-----------------------------------------------------------------------------
"""

In [39]:
# fit.predict(11, 20, typ="levels")
fit.forecast()

(array([3.22393334e+12]),
 array([6.15497719e+11]),
 array([[2.01757998e+12, 4.43028671e+12]]))